# 4. 해결과제2 
## 어린이보호구역 버퍼 별 데이터셋 생성

해결과제2는 보호구역을 기준으로 데이터들을 새롭게 전처리하여, 시설물의 효율성을 검정할 수 있는 데이터셋을 만들고자합니다.

### **[목차]**

**1. 어린이 교통사고 데이터**   
     - 어린이 교통사고(격자)
     
**2. 어린이보호구역 내 시설물 데이터**  
      - 무인교통단속카메라(주정차단속)  
      - 도로안전표지판  
      - 횡단보도  
      - 과속방지턱  
      - 신호등  
      - CCTV 설치 (C:어린이보호 D:차량방범 E:과속단속)  
      - 인도    
      - 횡단보도 (외부데이터)  
      - 도로분리대 (외부데이터)  
      - 과속방지턱 (외부데이터)  
      
**3. 어린이보호구역 내 도로면적 계산**  
      - 지적도_교차영역도로_100원 (QGIS 처리 데이터)
    
**4. 도로면적 대비 시설물 개수 데이터셋 만들기**   
  
 ** **
   
    
**어린이보호구역별로 전처리하여 만든 변수는 다음과 같다.** 
 - accident_cnt : 어린이 교통사고 수
 - sign_cnt : 도로안전표지판 수
 - CW_cnt : 구역내 모든 횡단보도 수
 - highCW_cnt : 고원식 횡단보도 수
 - bump_cnt : 과속방지턱 수
 - TL_cnt : 신호등 수
 - CCTV_cnt : CCTV설치 수와 무인교통단속카메라 합
 - SW_cnt : 인도 수
 - sep_cnt : 도로분리대 수

In [1]:
import folium
import json
import pandas as pd
import numpy as np
import geopandas as gpd
import fiona
import os

from shapely.geometry import Polygon, LineString, Point
from tqdm import tqdm

In [2]:
import warnings 
warnings.filterwarnings(action='ignore')

In [3]:
# 데이터 불러오기 
data2 = gpd.read_file('2.오산시_어린이교통사고_격자.geojson')
data15 = pd.read_csv('15.오산시_무인교통단속카메라.csv')
data16 = pd.read_csv('16.오산시_도로안전표지표준데이터.csv')
data17 = gpd.read_file('17.오산시_횡단보도.geojson')
data18 = pd.read_csv('18.오산시_과속방지턱표준데이터.csv')
data19 = gpd.read_file('19.오산시_신호등.geojson') 
data20 = pd.read_csv('20.오산시_CCTV설치현황.csv')
data21 = gpd.read_file('21.오산시_인도.geojson')

data31 = gpd.read_file("31.오산시_법정경계(시군구).geojson") #시각화시 오산시의 경계 표시 목적

In [4]:
## 외부데이터
crosswalk = pd.read_csv('경기도_오산시_횡단보도.csv', encoding = 'cp949') # 오산시 횡단보도 데이터
road_sp = gpd.read_file('Z_NGII_N3L_C0520000.shp') # 도로분리대 (전국) 데이터
bump = pd.read_csv('오산시 과속방지턱_LOCALDATA.csv') # 오산시 과속방지턱 데이터 

In [5]:
s_zone = gpd.read_file("어린이보호구역버퍼.geojson")
s_zone.head()

시설종류     시설명                                           geometry
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...

In [6]:
# 어린이보호구역의 분포 파악을 위한 지도 시각화

center = [37.165397, 127.048396]
m = folium.Map(location=center, zoom_start=13,tiles='cartodbpositron')
style1 = {'fillColor': False, 'color': '#475974'} #짙은남색
style2 = {'fillColor': '#ED9253', 'color': '#ED9253'} #주황색
style3 = {'fillColor': '#F15F5F', 'color': '#F15F5F'} #붉은색

folium.GeoJson(data=data31["geometry"], style_function=lambda x:style1).add_to(m) #오산시경계
folium.GeoJson(data=s_zone["geometry"], style_function=lambda x:style2).add_to(m)

m

## 1. 어린이 교통사고 데이터

In [7]:
data2.head()

gid  accident_cnt                                           geometry
0  다사551085             0  MULTIPOLYGON (((126.99422 37.17418, 126.99421 ...
1  다사551086             0  MULTIPOLYGON (((126.99421 37.17508, 126.99420 ...
2  다사551087             0  MULTIPOLYGON (((126.99420 37.17599, 126.99420 ...
3  다사551088             0  MULTIPOLYGON (((126.99420 37.17689, 126.99419 ...
4  다사552085             0  MULTIPOLYGON (((126.99534 37.17419, 126.99534 ...

In [8]:
# 어린이보호구역별 겹치는(intersect) 모든 격자의 사고수 계산(합)
cnt_in_polys = []
for i in tqdm(range(s_zone.shape[0])):
    buf = s_zone['geometry'].iloc[i]
    idx = data2['geometry'].intersects(buf)
    cnt_in_polys.append(sum(data2.accident_cnt[idx]))
    
s_zone['accident_cnt'] = cnt_in_polys
s_zone.head()

100%|██████████| 91/91 [00:01<00:00, 45.85it/s]


시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  
0             0  
1             0  
2             2  
3             8  
4             5

## 2. 어린이보호구역 내 시설물 데이터
### 1) 무인교통단속카메라 

In [9]:
data15.head()

도로노선명 도로노선방향          설치장소명   단속구분     설치위치_경도    설치위치_위도
0  궐리사로    양방향  궐동-법원앞(법원사거리)  불법주정차  127.059357  37.159313
1  역광장로    양방향       원동-오산역광장  불법주정차  127.067796  37.145409
2  궐리사로    양방향       궐동-제일하이빌  불법주정차  127.062386  37.159198
3  궐리사로    양방향      궐리사 주차장 앞  불법주정차  127.061920  37.158559
4   운암로    양방향    부산동-운천초교 입구  불법주정차  127.077991  37.156216

In [10]:
# 공간데이터 분석을 위해 좌표를 geometry 형식으로 변환
data15['설치위치_경도'] = data15['설치위치_경도'].astype(float)
data15['설치위치_위도'] = data15['설치위치_위도'].astype(float)
data15['geometry'] = data15.apply(lambda row : Point([row['설치위치_경도'], row['설치위치_위도']]), axis=1)

pts = gpd.GeoDataFrame(data15['geometry'], geometry='geometry')

In [11]:
# 어린이보호구역과 겹치는(intersect) 단속카메라 개수 세기
pts_in_polys = []

for i, poly in s_zone.iterrows():
    pts_in_this_poly = []

    for j, pt in pts.iterrows():
        if poly.geometry.intersects(pt.geometry):
            pts_in_this_poly.append(pt.geometry)
            pts = pts.drop([j])

    pts_in_polys.append(len(pts_in_this_poly))

s_zone['UCCTV_cnt'] = gpd.GeoSeries(pts_in_polys)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  UCCTV_cnt  
0             0          0  
1             0          0  
2             2          1  
3             8          0  
4             5          0

### 2) 도로안전표지판

In [12]:
data16.head()

표지일련번호        표지종별         lon        lat
0  ER-400[봉담동탄고속도로]-상-60     2방향예고표지  127.069227  37.182663
1      NR-1[경기대로]-하-1982      시/군계표지  127.040826  37.197859
2   UR(오산시)-16[남부대로]-상-5  3방향도로명예고표지  127.070216  37.135929
3   UR(오산시)-16[남부대로]-하-3       3방향표지  127.064316  37.135531
4   UR(오산시)-16[남부대로]-하-4     3방향예고표지  127.051717  37.134248

In [13]:
#안전표지판 위치를 geometry 형식으로 변환
data16['lon'] = data16['lon'].astype(float)
data16['lat'] = data16['lat'].astype(float)
data16['geometry'] = data16.apply(lambda row : Point([row['lon'], row['lat']]), axis=1)

pts = gpd.GeoDataFrame(data16['geometry'], geometry='geometry')

In [14]:
#어린이보호구역과 겹치는(intersect) 모든 표지판 개수 세기
pts_in_polys = []

for i, poly in s_zone.iterrows():
    pts_in_this_poly = []

    for j, pt in pts.iterrows():
        if poly.geometry.intersects(pt.geometry):
            pts_in_this_poly.append(pt.geometry)
            pts = pts.drop([j])

    pts_in_polys.append(len(pts_in_this_poly))

s_zone['sign_cnt'] = gpd.GeoSeries(pts_in_polys)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  UCCTV_cnt  sign_cnt  
0             0          0         0  
1             0          0         0  
2             2          1         2  
3             8          0         0  
4             5          0         1

### 3) 횡단보도

#### ㄱ. 기존 횡단보도 데이터

In [15]:
data17.head() 

OBJECTID                                           geometry
0         2  MULTIPOLYGON (((127.06170 37.15704, 127.06178 ...
1         3  MULTIPOLYGON (((127.03174 37.19499, 127.03176 ...
2         4  MULTIPOLYGON (((127.05525 37.15645, 127.05533 ...
3         5  MULTIPOLYGON (((127.04935 37.13434, 127.04939 ...
4         6  MULTIPOLYGON (((127.06216 37.14973, 127.06228 ...

In [16]:
#어린이보호구역과 겹치는(intersect) 모든 횡단보도 개수 계산
pts = gpd.GeoDataFrame(data17['geometry'], geometry='geometry')

pts_in_polys = []

for i, poly in s_zone.iterrows():
    pts_in_this_poly = []

    for j, pt in pts.iterrows():
        if poly.geometry.intersects(pt.geometry):
            pts_in_this_poly.append(pt.geometry)
            pts = pts.drop([j])

    pts_in_polys.append(len(pts_in_this_poly))

s_zone['CW_cnt'] = gpd.GeoSeries(pts_in_polys)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  UCCTV_cnt  sign_cnt  CW_cnt  
0             0          0         0       0  
1             0          0         0       0  
2             2          1         2       0  
3             8          0         0       6  
4             5          0         1       1

여러 선행연구에서 횡단보도를 고원식 유무에 따라 나눠 분석한 것을 확인하였습니다. 이를 근거로 본 연구에서도 횡단보도의 종류를 나누고, 어린이 교통사고에 끼치는 영향을 각각 살펴보고자 합니다.  
하지만 주어진 횡단보도 데이터는 고원식 횡단보도인지 알 수 없어, 추가적으로 외부데이터를 사용했습니다.


#### ㄴ. 횡단보도 외부데이터 
해당 데이터를 기반으로, 기존 횡단보도 데이터가 충분히 적절한지, 고원식 횡단보도의 분포는 어떠한지 확인해보겠습니다.

In [17]:
crosswalk = pd.read_csv('경기도_오산시_횡단보도.csv',encoding = 'cp949')
crosswalk.head()

시도명 시군구명  도로명  소재지도로명주소            소재지지번주소 횡단보도관리번호  횡단보도종류  자전거횡단도겸용여부  \
0  경기도  오산시  발안로       NaN  경기도 오산시 가수동 115-2    A0001       1         NaN   
1  경기도  오산시  가수로       NaN   경기도 오산시 가수동 13-4    A0002       1         NaN   
2  경기도  오산시  가수로       NaN   경기도 오산시 가수동 13-4    A0003       1         NaN   
3  경기도  오산시  가수로       NaN   경기도 오산시 가수동 13-4    A0004       1         NaN   
4  경기도  오산시  발안로       NaN  경기도 오산시 가수동 139-2    A0005       1         NaN   

  고원식적용여부         위도  ...  음향신호기설치여부  녹색신호시간  적색신호시간  교통섬유무 보도턱낮춤여부  점자블록유무  \
0       N  37.146229  ...        NaN     NaN     NaN      N     NaN       N   
1       N  37.146684  ...        NaN     NaN     NaN      N     NaN       Y   
2       N  37.146553  ...        NaN     NaN     NaN      N     NaN       N   
3       N  37.146481  ...        NaN     NaN     NaN      N     NaN       Y   
4       N  37.146235  ...        NaN     NaN     NaN      N     NaN       N   

   집중조명시설유무    관리기관명       관리기관전화번호     데이터기준일자  
0       NaN  오산시 교통과  031-8036-7726  2020-10-08  
1       NaN  오산시 교통과  031-8036-7726  2020-10-08  
2       NaN  오산시 교통과  031-8036-7726  2020-10-08  
3       NaN  오산시 교통과  031-8036-7726  2020-10-08  
4       NaN  오산시 교통과  031-8036-7726  2020-10-08  

[5 rows x 26 columns]

In [18]:
#기존 데이터와 외부데이터의 정보량 비교
print(data17.shape) #1205
print(crosswalk.shape) # 1396

(1205, 2)
(1396, 26)


In [19]:
#횡단보도(외부) 위치 geometry 형식으로 변환
crosswalk['경도'] = crosswalk['경도'].astype(float)
crosswalk['위도'] = crosswalk['위도'].astype(float)
crosswalk['geometry'] = crosswalk.apply(lambda row: Point([row['경도'], row['위도']]), axis=1)

pts = gpd.GeoDataFrame(crosswalk['geometry'], geometry = 'geometry')

In [20]:
# 내부, 외부 횡단보도 데이터의 시각적 비교

center = [37.165397, 127.048396]
m = folium.Map(location=center, zoom_start=15,tiles='cartodbpositron')
style1 = {'fillColor': '#475974', 'color': '#475974'} #짙은남색
style2 = {'fillColor': '#ED9253', 'color': '#ED9253'} #주황색
style3 = {'fillColor': '#F15F5F', 'color': '#F15F5F'} #붉은색

folium.GeoJson(data=s_zone["geometry"], style_function=lambda x:style2).add_to(m) #어린이보호구역
folium.GeoJson(data=data17["geometry"], style_function=lambda x:style1).add_to(m) #기존데이터
for i in range(len(crosswalk)):
    folium.Circle(
        location=[crosswalk.iloc[i]['위도'], crosswalk.iloc[i]['경도']],
        radius=2,
        color='#F15F5F', fill=False
    ).add_to(m)  #외부데이터

m

시각화로만 어떤 데이터가 더 좋은지 해석하기가 어려워, 외부데이터로도 어린이보호구역에 겹치는 횡단보도의 개수를 계산했습니다.

In [21]:
#어린이보호구역과 겹치는(intersect) 횡단보도(외부) 개수 계산
pts_in_polys = []

for i, poly in s_zone.iterrows():
    pts_in_this_poly = []

    for j, pt in pts.iterrows():
        if poly.geometry.intersects(pt.geometry):
            pts_in_this_poly.append(pt.geometry)
            pts = pts.drop([j])

    pts_in_polys.append(len(pts_in_this_poly))

s_zone['CW2_cnt'] = gpd.GeoSeries(pts_in_polys)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  UCCTV_cnt  sign_cnt  CW_cnt  CW2_cnt  
0             0          0         0       0        0  
1             0          0         0       0        0  
2             2          1         2       0        0  
3             8          0         0       6       10  
4             5          0         1       1        5

확인결과 특정 데이터가 다른 하나의 데이터를 포함하고 있는 구조가 아니었고, 제공 데이터와 외부데이터 중 어떤 것이 더 의미있는지는 어린이보호구역에 따라 달랐습니다.  
이에 저희 팀은 두 자료 중에 하나를 취해 전체적으로 적용하기 보다는 보호구역에 따라 더 적절한것을 고르는 것이 좋겠다고 생각했습니다.  
따라서 본 연구는 **CW_cnt와 CW2_cnt의 값을 보호구역별로 비교하여 그 개수가 더 큰 값을 해당 보호구역의 횡단보도 개수로 정했습니다.**

In [22]:
s_zone['CW_cnt'] = s_zone.apply(lambda row: max(row['CW_cnt'], row['CW2_cnt']), axis=1)
s_zone = s_zone.drop('CW2_cnt', axis=1)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  UCCTV_cnt  sign_cnt  CW_cnt  
0             0          0         0       0  
1             0          0         0       0  
2             2          1         2       0  
3             8          0         0      10  
4             5          0         1       5

### 4) 고원식 횡단보도 
고원식횡단보도인 경우를 필터링해 그 개수를 계산했습니다.

In [23]:
crosswalk.loc[(crosswalk['고원식적용여부']=='Y'), :].shape # 78
high_cw = crosswalk.loc[(crosswalk['고원식적용여부']=='Y'), :]
high_cw.head()

시도명 시군구명      도로명  소재지도로명주소            소재지지번주소 횡단보도관리번호  횡단보도종류  \
47   경기도  오산시      가수로       NaN   경기도 오산시 가수동 48-4    A0048       1   
104  경기도  오산시   가장산업서로       NaN  경기도 오산시 가장동 405-1    A0105       1   
107  경기도  오산시  가장산업서북로       NaN  경기도 오산시 가장동 405-1    A0108       1   
108  경기도  오산시  가장산업서북로       NaN  경기도 오산시 가장동 405-1    A0109       1   
114  경기도  오산시   가장산업서로       NaN  경기도 오산시 가장동 405-4    A0115       1   

     자전거횡단도겸용여부 고원식적용여부         위도  ...  녹색신호시간  적색신호시간  교통섬유무  보도턱낮춤여부  \
47          NaN       Y  37.145646  ...     NaN     NaN      N      NaN   
104         NaN       Y  37.164575  ...     NaN     NaN      N        Y   
107         NaN       Y  37.166577  ...     NaN     NaN      N        Y   
108         NaN       Y  37.167449  ...     NaN     NaN      N        Y   
114         NaN       Y  37.164179  ...     NaN     NaN      N        Y   

    점자블록유무  집중조명시설유무    관리기관명       관리기관전화번호     데이터기준일자  \
47       N       NaN  오산시 교통과  031-8036-7726  2020-10-08   
104      Y       NaN  오산시 교통과  031-8036-7726  2020-10-08   
107      Y       NaN  오산시 교통과  031-8036-7726  2020-10-08   
108      Y       NaN  오산시 교통과  031-8036-7726  2020-10-08   
114      Y       NaN  오산시 교통과  031-8036-7726  2020-10-08   

                            geometry  
47    POINT (127.0486348 37.1456461)  
104  POINT (127.0294671 37.16457489)  
107  POINT (127.0296677 37.16657744)  
108     POINT (127.030504 37.167449)  
114  POINT (127.0343954 37.16417935)  

[5 rows x 27 columns]

In [24]:
## 고원식 횡단보도 포함 모든 횡단보도 데이터를의 지도 시각화

for i in range(len(high_cw)):
    folium.Circle(
        location=[high_cw.iloc[i]['위도'], high_cw.iloc[i]['경도']],
        radius=10,
        popup = '고원식 횡단보도',
        color='darkred', fill=True, fill_color='darkred'
    ).add_to(m)
m

In [25]:
#어린이보호구역과 겹치는(intersect) 고원식횡단보도의 개수 계산

pts = gpd.GeoDataFrame(high_cw['geometry'], geometry = 'geometry')

pts_in_polys = []

for i, poly in s_zone.iterrows():
    pts_in_this_poly = []

    for j, pt in pts.iterrows():
        if poly.geometry.intersects(pt.geometry):
            pts_in_this_poly.append(pt.geometry)
            pts = pts.drop([j])

    pts_in_polys.append(len(pts_in_this_poly))

s_zone['highCW_cnt'] = gpd.GeoSeries(pts_in_polys)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  UCCTV_cnt  sign_cnt  CW_cnt  highCW_cnt  
0             0          0         0       0           0  
1             0          0         0       0           0  
2             2          1         2       0           0  
3             8          0         0      10           6  
4             5          0         1       5           0

### 5) 과속방지턱
#### ㄱ. 기존데이터

In [26]:
data18.tail() 

도로명           설치장소명  과속방지턱높이  과속방지턱폭  과속방지턱연장 보차분리여부 연속형여부     설치위치_경도  \
24  수청로  수청동 제2어린이공원 부근       10     3.6      6.3      Y     N  127.058726   
25  수청로        제주오피스텔 앞       10     3.6      6.4      Y     N  127.058285   
26  양산로         슬라이트 부근       10     3.6      6.2      N     Y  127.021448   
27  수청로     세교10단지 입구 전       10     3.6      5.4      Y     Y  127.051041   
28  수청로    필봉초등학교 입구 부근       10     3.6      5.4      Y     Y  127.051935   

      설치위치_위도  
24  37.173895  
25  37.175157  
26  37.195724  
27  37.178863  
28  37.178089

**데이터가 28개 밖에 없어 외부데이터를 사용하기로 하였습니다.**

#### ㄴ. 외부데이터

In [27]:
# 과속방지턱 외부데이터
bump = pd.read_csv('오산시 과속방지턱_LOCALDATA.csv')
bump.tail()

번호  과속방지턱관리번호       도로명  시도명 시군구명  소재지도로명주소           소재지지번주소  \
980  981        451  황새로149번길  경기도  오산시       NaN   경기도 오산시 누읍동 649   
981  982        452  황새로149번길  경기도  오산시       NaN  경기도 오산시 누읍동 60-2   
982  983        453  황새로149번길  경기도  오산시       NaN  경기도 오산시 누읍동 28-1   
983  984        454      동부대로  경기도  오산시       NaN   경기도 오산시 청호동 331   
984  985        455      동부대로  경기도  오산시       NaN   경기도 오산시 청호동 330   

                   설치장소    과속방지턱재료 과속방지턱형태구분  ...  도로유형구분  규격여부         위도  \
980    황새로149번길 41 7시방면  아스팔트 콘크리트       원호형  ...      소로     N  37.139202   
981          누리산업 정문 좌측  아스팔트 콘크리트       원호형  ...      일반     Y  37.139847   
982          누리산업 정문 우측  아스팔트 콘크리트       원호형  ...      일반     Y  37.139846   
983    GS아파트정문 버스정류장 정면  아스팔트 콘크리트       원호형  ...      소로     N  37.131996   
984  오산자이아파트 103동 우측 도로  아스팔트 콘크리트       원호형  ...      일반     Y  37.132232   

             경도 보차분리여부  연속형여부  과속방지턱설치연도     관리기관명       관리기관전화번호     데이터기준일자  
980  127.056602      Y      N        NaN  경기도 오산시청  031-8036-7702  2020-12-09  
981  127.056979      N      N        NaN  경기도 오산시청  031-8036-7702  2020-12-09  
982  127.057179      N      N        NaN  경기도 오산시청  031-8036-7702  2020-12-09  
983  127.079822      Y      N        NaN  경기도 오산시청  031-8036-7702  2020-12-09  
984  127.081538      Y      N        NaN  경기도 오산시청  031-8036-7702  2020-12-09  

[5 rows x 23 columns]

In [28]:
#공간 분석을 위해 과속방지턱 위치를 geometry 형식으로 변환

bump['경도'] = bump['경도'].astype(float)
bump['위도'] = bump['위도'].astype(float)
bump['geometry'] = bump.apply(lambda row : Point([row['경도'], row['위도']]), axis=1)

pts = gpd.GeoDataFrame(bump['geometry'], geometry='geometry')

In [29]:
#어린이보호구역과 겹치는(intersect) 과속방지턱의 개수 세기

pts_in_polys = []

for i, poly in s_zone.iterrows():
    pts_in_this_poly = []

    for j, pt in pts.iterrows():
        if poly.geometry.intersects(pt.geometry):
            pts_in_this_poly.append(pt.geometry)
            pts = pts.drop([j])

    pts_in_polys.append(len(pts_in_this_poly))

s_zone['bump_cnt'] = gpd.GeoSeries(pts_in_polys)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  UCCTV_cnt  sign_cnt  CW_cnt  highCW_cnt  bump_cnt  
0             0          0         0       0           0         0  
1             0          0         0       0           0         1  
2             2          1         2       0           0         0  
3             8          0         0      10           6         7  
4             5          0         1       5           0         3

### 6) 신호등

In [30]:
data19.head()

OBJECTID                    geometry
0         1  POINT (127.07160 37.14407)
1         2  POINT (127.08149 37.12849)
2         3  POINT (127.03978 37.16155)
3         4  POINT (127.03999 37.16168)
4         5  POINT (127.07838 37.14296)

In [31]:
pts = gpd.GeoDataFrame(data19['geometry'], geometry='geometry')

In [32]:
#어린이보호구역과 겹치는(intersect) 신호등 개수 세기

pts_in_polys = []

for i, poly in s_zone.iterrows():
    pts_in_this_poly = []

    for j, pt in pts.iterrows():
        if poly.geometry.intersects(pt.geometry):
            pts_in_this_poly.append(pt.geometry)
            pts = pts.drop([j])

    pts_in_polys.append(len(pts_in_this_poly))

s_zone['TL_cnt'] = gpd.GeoSeries(pts_in_polys)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  UCCTV_cnt  sign_cnt  CW_cnt  highCW_cnt  bump_cnt  TL_cnt  
0             0          0         0       0           0         0       0  
1             0          0         0       0           0         1       0  
2             2          1         2       0           0         0       0  
3             8          0         0      10           6         7       4  
4             5          0         1       5           0         3       0

### 7) CCTV

In [33]:
data20.head()

CCTV 유형코드     설치위치_도로명주소    설치위치_위도     설치위치_경도
0         A  성호대로55번길 31-2  37.151836  127.067541
1         A    성호대로93번길 45  37.152812  127.071702
2         C    성호대로93번길 26  37.151167  127.071677
3         A  운천로165번길 52-1  37.157164  127.075991
4         A     운천로165번길 5  37.156461  127.077273

In [34]:
#cctv 유형코드 기준으로 필터링
data20_CDE =data20[(data20['CCTV 유형코드']!='A')&(data20['CCTV 유형코드']!='B')&(data20['CCTV 유형코드']!=' B')]
data20_CDE['CCTV 유형코드'].unique()

array(['C', 'BC', 'D', 'E'], dtype=object)

In [35]:
#CCTV설치 위치를 geometry 형식으로 변환

data20_CDE['설치위치_경도'] = data20_CDE['설치위치_경도'].astype(float)
data20_CDE['설치위치_위도'] = data20_CDE['설치위치_위도'].astype(float)
data20_CDE['geometry'] = data20_CDE.apply(lambda row : Point([row['설치위치_경도'], row['설치위치_위도']]), axis=1)

pts = gpd.GeoDataFrame(data20_CDE['geometry'], geometry='geometry')

In [36]:
#어린이보호구역과 겹치는(intersect) CCTV 개수 계산

pts_in_polys = []

for i, poly in s_zone.iterrows():
    pts_in_this_poly = []

    for j, pt in pts.iterrows():
        if poly.geometry.intersects(pt.geometry):
            pts_in_this_poly.append(pt.geometry)
            pts = pts.drop([j])

    pts_in_polys.append(len(pts_in_this_poly))

s_zone['CCTV_cnt'] = gpd.GeoSeries(pts_in_polys)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  UCCTV_cnt  sign_cnt  CW_cnt  highCW_cnt  bump_cnt  TL_cnt  \
0             0          0         0       0           0         0       0   
1             0          0         0       0           0         1       0   
2             2          1         2       0           0         0       0   
3             8          0         0      10           6         7       4   
4             5          0         1       5           0         3       0   

   CCTV_cnt  
0         0  
1         0  
2         0  
3         3  
4         0

In [37]:
# UCCTV_cnt(주정차단속)와 CCTV_cnt를 합한 새로운 CCTV_cnt 변수 만들기
s_zone['CCTV_cnt'] = s_zone['UCCTV_cnt'] + s_zone['CCTV_cnt']
s_zone = s_zone.drop('UCCTV_cnt', axis=1)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  sign_cnt  CW_cnt  highCW_cnt  bump_cnt  TL_cnt  CCTV_cnt  
0             0         0       0           0         0       0         0  
1             0         0       0           0         1       0         0  
2             2         2       0           0         0       0         1  
3             8         0      10           6         7       4         3  
4             5         1       5           0         3       0         0

### 8) 인도

In [38]:
data21.head()

UFID    QUAL    BYYN    KIND  \
0  TRN0400000002N7T0  SWQ003  BYC001  SWK001   
1  TRN0400000002N79G  SWQ003  BYC001  SWK001   
2  TRN0400000002N7LS  SWQ003  BYC001  SWK001   
3  TRN0400000002NAR1  SWQ001  BYC001  SWK001   
4  TRN0400000003E7DC  SWQ001  BYC001  SWK001   

                                            geometry  
0  MULTILINESTRING ((127.05144 37.14183, 127.0514...  
1  MULTILINESTRING ((127.04907 37.14108, 127.0490...  
2  MULTILINESTRING ((127.05210 37.14163, 127.0521...  
3  MULTILINESTRING ((127.07471 37.14870, 127.0747...  
4  MULTILINESTRING ((127.07466 37.14988, 127.0746...

In [39]:
#어린이보호구역과 겹치는(intersect) 인도 개수 계산

pts = gpd.GeoDataFrame(data21['geometry'], geometry='geometry')

pts_in_polys = []

for i, poly in s_zone.iterrows():
    pts_in_this_poly = []

    for j, pt in pts.iterrows():
        if poly.geometry.intersects(pt.geometry):
            pts_in_this_poly.append(pt.geometry)
            pts = pts.drop([j])

    pts_in_polys.append(len(pts_in_this_poly))

s_zone['SW_cnt'] = gpd.GeoSeries(pts_in_polys)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  sign_cnt  CW_cnt  highCW_cnt  bump_cnt  TL_cnt  CCTV_cnt  \
0             0         0       0           0         0       0         0   
1             0         0       0           0         1       0         0   
2             2         2       0           0         0       0         1   
3             8         0      10           6         7       4         3   
4             5         1       5           0         3       0         0   

   SW_cnt  
0       0  
1       3  
2       2  
3       3  
4       5

### 9) 도로분리대

In [40]:
separator =gpd.read_file('Z_NGII_N3L_C0520000.shp',encoding='euc-kr')
separator.head()

UFID    STRU  SCLS  FMTA  \
0  TRN0700000000001F  MSS002  None  None   
1  TRN0700000000002G  MSS002  None  None   
2  TRN0700000000003H  MSS003  None  None   
3  TRN0700000000004I  MSS002  None  None   
4  TRN0700000000005J  MSS002  None  None   

                                            geometry  
0  LINESTRING (330458.478 378041.635, 330507.231 ...  
1  LINESTRING (324733.176 380299.947, 324699.671 ...  
2  LINESTRING (297236.204 404358.597, 297331.349 ...  
3  LINESTRING (318316.245 390874.429, 318313.410 ...  
4  LINESTRING (310325.047 408579.468, 310366.019 ...

In [41]:
#기존 좌표계 확인
print(separator.crs) #NONE

separator.crs = {'init':'epsg:5181'} # 지정된 좌표계가 없어 적절한 좌표계(5181)를 직접 지정했습니다.
print(separator.crs)

separator = separator.to_crs({'init':'epsg:4326'}) #분석 기준애 맞춰 epsg:4326 좌표계로 변환했습니다.

print(separator.crs) #좌표계 변환을 확인했습니다.

separator.head()

None
+init=epsg:5181 +type=crs
+init=epsg:4326 +type=crs


UFID    STRU  SCLS  FMTA  \
0  TRN0700000000001F  MSS002  None  None   
1  TRN0700000000002G  MSS002  None  None   
2  TRN0700000000003H  MSS003  None  None   
3  TRN0700000000004I  MSS002  None  None   
4  TRN0700000000005J  MSS002  None  None   

                                            geometry  
0  LINESTRING (128.46352 36.89212, 128.46406 36.8...  
1  LINESTRING (128.39968 36.91324, 128.39931 36.9...  
2  LINESTRING (128.09429 37.13322, 128.09536 37.1...  
3  LINESTRING (128.32935 37.00933, 128.32932 37.0...  
4  LINESTRING (128.24219 37.16980, 128.24265 37.1...

In [42]:
## 오산시 경계 내에 있는 데이터만 필터링
separator = gpd.sjoin(separator, data31, op = 'within')
separator.head()

UFID    STRU  SCLS  FMTA  \
35601  TRN0700000000RJXL  MSS003  None  None   
35602  TRN0700000000RJYM  MSS003  None  None   
35603  TRN0700000000RJZN  MSS003  None  None   
35605  TRN0700000000RK1Q  MSS001  None  None   
35607  TRN0700000000RK3S  MSS003  None  None   

                                                geometry  index_right SIG_CD  \
35601  LINESTRING (127.04968 37.13419, 127.04984 37.1...            0  41370   
35602  LINESTRING (127.07329 37.13590, 127.07361 37.1...            0  41370   
35603  LINESTRING (127.07406 37.14272, 127.07421 37.1...            0  41370   
35605  LINESTRING (127.07885 37.15000, 127.07921 37.1...            0  41370   
35607  LINESTRING (127.03977 37.17827, 127.03927 37.1...            0  41370   

      SIG_KOR_NM  
35601        오산시  
35602        오산시  
35603        오산시  
35605        오산시  
35607        오산시

In [43]:
#어린이보호구역과 겹치는(intersect) 도로분리대 개수 계산
pts = gpd.GeoDataFrame(separator['geometry'], geometry='geometry')

pts_in_polys = []

for i, poly in s_zone.iterrows():
    pts_in_this_poly = []

    for j, pt in pts.iterrows():
        if poly.geometry.intersects(pt.geometry):
            pts_in_this_poly.append(pt.geometry)
            pts = pts.drop([j])

    pts_in_polys.append(len(pts_in_this_poly))

s_zone['sep_cnt'] = gpd.GeoSeries(pts_in_polys)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
2  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
3  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
4  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   

   accident_cnt  sign_cnt  CW_cnt  highCW_cnt  bump_cnt  TL_cnt  CCTV_cnt  \
0             0         0       0           0         0       0         0   
1             0         0       0           0         1       0         0   
2             2         2       0           0         0       0         1   
3             8         0      10           6         7       4         3   
4             5         1       5           0         3       0         0   

   SW_cnt  sep_cnt  
0       0        0  
1       3        0  
2       2        1  
3       3        0  
4       5        0

In [44]:
#만든 데이터셋의 특징 정리
s_zone.describe()

accident_cnt   sign_cnt     CW_cnt  highCW_cnt   bump_cnt     TL_cnt  \
count     91.000000  91.000000  91.000000   91.000000  91.000000  91.000000   
mean       2.505495   0.549451   2.494505    0.351648   2.340659   1.670330   
std        2.778383   1.024844   3.321223    1.036807   2.324841   3.861649   
min        0.000000   0.000000   0.000000    0.000000   0.000000   0.000000   
25%        0.000000   0.000000   0.000000    0.000000   0.000000   0.000000   
50%        2.000000   0.000000   2.000000    0.000000   2.000000   0.000000   
75%        4.000000   1.000000   4.000000    0.000000   4.000000   2.000000   
max       13.000000   5.000000  21.000000    6.000000  11.000000  27.000000   

        CCTV_cnt    SW_cnt    sep_cnt  
count  91.000000  91.00000  91.000000  
mean    1.263736   2.67033   0.263736  
std     0.998167   3.21474   0.867117  
min     0.000000   0.00000   0.000000  
25%     1.000000   0.00000   0.000000  
50%     1.000000   2.00000   0.000000  
75%     2.000000   4.00000   0.000000  
max     4.000000  15.00000   7.000000

## 3. 어린이보호구역 내 도로 면적 계산
어린이 보호구역에 얼마나 많은 도로가 있는지도 시설물에 영향을 줄것이라 판단하여 도로면적을 분석에 고려하였습니다.

In [45]:
road = gpd.read_file("지적도_교차영역도로_100원.geojson") # QGIS 이용해 만든 어린이보호구역 도로 데이터를 이용합니다.
road.head()

PNU    JIBUN  시설종류      시설명 CCTV설치여부  CCTV설치대수  보호구역도로폭  \
0  4137011100101510002  151-2 도   유치원  동탄우리유치원        Y         1        4   
1  4137011100101510002  151-2 도  어린이집  베스트어린이집        Y         1        3   
2  4137011100101510003  151-3 도   유치원  동탄우리유치원        Y         1        4   
3  4137011100101510003  151-3 도  어린이집  베스트어린이집        Y         1        3   
4  4137011100101510004  151-4 도   유치원  동탄우리유치원        Y         1        4   

      보호구역_경도    보호구역_위도                                           geometry  
0  127.060252  37.196997  MULTIPOLYGON (((127.06077 37.19778, 127.06070 ...  
1  127.061423  37.197877  MULTIPOLYGON (((127.06091 37.19805, 127.06086 ...  
2  127.060252  37.196997  MULTIPOLYGON (((127.06064 37.19770, 127.06064 ...  
3  127.061423  37.197877  MULTIPOLYGON (((127.06064 37.19770, 127.06064 ...  
4  127.060252  37.196997  MULTIPOLYGON (((127.06055 37.19781, 127.06056 ...

EPSG:4326 좌표는 미터단위로 인식하지 않기 때문에, 좌표 변환 없이 면적을 계산할 경우 그 의미를 직관적으로 파악하기가 어렵습니다.  
따라서 본 분석에서는 미터단위 계산이 가능한 EPSG:5181좌표계로 데이터를 임시 변환하여 그 면적을 계산했습니다.  

In [46]:
pts = gpd.GeoDataFrame(road['geometry'], geometry='geometry') #좌표부분만 떼어 따로 저장합니디.
print(pts.crs) #4326임을 확인합니다.

pts = pts.to_crs({'init':'epsg:5181'}) #미터단위 계산을 위해 좌표를 변환했습니다.
print(pts.crs)

epsg:4326
+init=epsg:5181 +type=crs


In [47]:
#어린이보호구역과 겹치는(intersect) 도로 면적 계산

area_in_polys = []
for i in range(s_zone.shape[0]):
    indx_in_this_poly = []
    
    for j in range(road.shape[0]):
        if s_zone['시설명'][i]==road['시설명'][j]:
            indx_in_this_poly.append(j)
        
    area_in_polys.append(sum(pts.loc[indx_in_this_poly].area))
    
road_area = gpd.GeoSeries(area_in_polys)
road_area.head()

0     325.207585
1       0.000000
2     353.444653
3    7270.168067
4    3775.309522
dtype: float64

In [48]:
# 도로 면적 결과를 확인하기 위해 버퍼 자체의 넓이와 비교해보았습니다.

pts = gpd.GeoDataFrame(s_zone['geometry'], geometry='geometry') #어린이보호구역도 좌표계를 임시 변환하여 따로 저장합니다.

print(pts.crs)

pts = pts.to_crs({'init':'epsg:5181'}) 
print(pts.crs)

epsg:4326
+init=epsg:5181 +type=crs


In [49]:
#버퍼 자체의 면적 계산
s_zone_area=pts.area

#두 면적을 비교
# road_area가 더 큰 경우 버퍼보다 도로의 면적이 크다는 의미이므로, 계산이 잘못되었음을 의미합니다.
sum(road_area > s_zone_area)

0

In [50]:
#면적이 보호구역 전체 면적보다 큰 경우는 없었지만, 도로면적이 0인 곳이 있어 살펴보았습니다.
s_zone[road_area==0]

시설종류       시설명                                           geometry  \
1   초등학교    가수초등학교  POLYGON ((127.04908 37.14810, 127.04908 37.148...   
12  초등학교  오산원당초등학교  POLYGON ((127.09208 37.14226, 127.09208 37.142...   

    accident_cnt  sign_cnt  CW_cnt  highCW_cnt  bump_cnt  TL_cnt  CCTV_cnt  \
1              0         0       0           0         1       0         0   
12             0         0       0           0         0       0         1   

    SW_cnt  sep_cnt  
1        3        0  
12       0        0

두 학교 앞에는 지도상에 도로가 있고, 실제 어린이보호구역 데이터에는 도로 폭까지 명시되어 있습니다.  
하지만 지적도, LINK지도는 모두 해당 학교 앞 도로관련 데이터가 존재하지 않았습니다.  

본 데이터 분석에서는 모든 변수를 도로 면적으로 나누어 **도로면적 대비 분석**을 진행할 것이므로,  
**위의 두 행은 고려하지 않기로 하고, 삭제했습니다.**

In [51]:
# 도로면적이 0이 나온 데이터 삭제
s_zone = s_zone[(s_zone['시설명'] != '가수초등학교') & (s_zone['시설명'] != '오산원당초등학교')].reset_index(drop=True)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
2  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
3  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   
4  초등학교  삼미초등학교  POLYGON ((127.06140 37.19136, 127.06139 37.191...   

   accident_cnt  sign_cnt  CW_cnt  highCW_cnt  bump_cnt  TL_cnt  CCTV_cnt  \
0             0         0       0           0         0       0         0   
1             2         2       0           0         0       0         1   
2             8         0      10           6         7       4         3   
3             5         1       5           0         3       0         0   
4             0         0       0           0         0       0         1   

   SW_cnt  sep_cnt  
0       0        0  
1       2        1  
2       3        0  
3       5        0  
4       0        0

In [52]:
s_zone['road_area'] = road_area[road_area!=0].reset_index(drop=True)
s_zone.head()

시설종류     시설명                                           geometry  \
0  특수학교    성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1  초등학교  광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
2  초등학교  대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
3  초등학교  매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   
4  초등학교  삼미초등학교  POLYGON ((127.06140 37.19136, 127.06139 37.191...   

   accident_cnt  sign_cnt  CW_cnt  highCW_cnt  bump_cnt  TL_cnt  CCTV_cnt  \
0             0         0       0           0         0       0         0   
1             2         2       0           0         0       0         1   
2             8         0      10           6         7       4         3   
3             5         1       5           0         3       0         0   
4             0         0       0           0         0       0         1   

   SW_cnt  sep_cnt    road_area  
0       0        0   325.207585  
1       2        1   353.444653  
2       3        0  7270.168067  
3       5        0  3775.309522  
4       0        0  1514.567449

In [53]:
s_zone = gpd.GeoDataFrame(s_zone, geometry='geometry')
s_zone.to_file('어린이보호구역_시설물_데이터(면적포함).geojson', driver="GeoJSON",index=False)

## 4. 도로면적 대비 시설물 개수 데이터셋 만들기

In [54]:
# 데이터셋 값을 도로면적 대비 값으로 변환
for i in range(0,len(s_zone)):
    for j in range(3,12):
        if s_zone.iloc[i,j] != 0:
            s_zone.iloc[i,j] = s_zone.iloc[i,j] / s_zone.iloc[i,12]
        else:
            s_zone.iloc[i,j] = 0

In [55]:
s_zone2 = s_zone.drop('road_area', axis=1) #도로 면적을 고려했으므로, road_area 열은 제외 후 저장했습니다.
s_zone2

시설종류         시설명                                           geometry  \
0   특수학교        성심학교  POLYGON ((127.01865 37.17676, 127.01864 37.176...   
1   초등학교      광성초등학교  POLYGON ((127.04083 37.18420, 127.04083 37.184...   
2   초등학교      대호초등학교  POLYGON ((127.05901 37.15911, 127.05901 37.159...   
3   초등학교      매홀초등학교  POLYGON ((127.06441 37.16275, 127.06440 37.162...   
4   초등학교      삼미초등학교  POLYGON ((127.06140 37.19136, 127.06139 37.191...   
..   ...         ...                                                ...   
84  어린이집    시립세마어린이집  POLYGON ((127.04604 37.18461, 127.04604 37.184...   
85  어린이집     미래숲어린이집  POLYGON ((127.04551 37.14533, 127.04550 37.145...   
86  어린이집   시립은여울어린이집  POLYGON ((127.06799 37.17095, 127.06798 37.170...   
87  어린이집     설리반어린이집  POLYGON ((127.06217 37.16413, 127.06216 37.164...   
88  어린이집  세교복지타운어린이집  POLYGON ((127.04596 37.17775, 127.04596 37.177...   

    accident_cnt  sign_cnt    CW_cnt  highCW_cnt  bump_cnt    TL_cnt  \
0       0.000000  0.000000  0.000000    0.000000  0.000000  0.000000   
1       0.005659  0.005659  0.000000    0.000000  0.000000  0.000000   
2       0.001100  0.000000  0.001375    0.000825  0.000963  0.000550   
3       0.001324  0.000265  0.001324    0.000000  0.000795  0.000000   
4       0.000000  0.000000  0.000000    0.000000  0.000000  0.000000   
..           ...       ...       ...         ...       ...       ...   
84      0.000138  0.000000  0.000829    0.000138  0.000000  0.000000   
85      0.000956  0.000000  0.000956    0.000478  0.000956  0.000000   
86      0.000698  0.000233  0.000930    0.000000  0.000000  0.000698   
87      0.000487  0.000000  0.000162    0.000000  0.000487  0.000000   
88      0.002818  0.000000  0.000403    0.000000  0.000403  0.000000   

    CCTV_cnt    SW_cnt   sep_cnt  
0   0.000000  0.000000  0.000000  
1   0.002829  0.005659  0.002829  
2   0.000413  0.000413  0.000000  
3   0.000000  0.001324  0.000000  
4   0.000660  0.000000  0.000000  
..       ...       ...       ...  
84  0.000276  0.000691  0.000000  
85  0.000478  0.000478  0.000000  
86  0.000233  0.001512  0.000000  
87  0.000000  0.000325  0.000000  
88  0.000805  0.000805  0.000000  

[89 rows x 12 columns]

In [56]:
s_zone2.to_csv('어린이보호구역_시설물_데이터(면적고려).csv', index=False, header=True)

In [57]:
s_zone2 = gpd.GeoDataFrame(s_zone2, geometry='geometry')
s_zone2.to_file('어린이보호구역_시설물_데이터(면적고려).geojson', driver="GeoJSON",index=False)